## Download latest data

In [1]:
import requests

url="https://data.taipei/api/dataset/70a6216e-3730-4d1d-b334-62fca2dd71cd/resource/3bd658e7-8e8a-446b-8df5-89b2b896ff97/download"
response=requests.get(url)
print(type(response))

<class 'requests.models.Response'>


In [ ]:
import csv
import io
taipei_csv_data = io.StringIO(response.text)
reader=csv.reader(taipei_csv_data)
# print(type(reader))
# print(reader)
for row in reader:
    print(row)


## postgreSQL

In [4]:
# 連接 PostgreSQL 資料庫
conn = psycopg2.connect(
    dbname="postgres", 
    user="postgres", 
    password="mysecretpassword", 
    host="localhost", 
    port="5432"
)
cursor = conn.cursor()

# 建立表格（如果尚未存在）
cursor.execute('''
    CREATE TABLE IF NOT EXISTS my_table (
        shelter_ID TEXT,
        address TEXT,
        latitude FLOAT,
        longitude FLOAT,
        u_floor INTEGER,
        p_available INTEGER
    )
''')

# 跳過標題行
header = next(reader)

# 讀取並處理資料
for row in reader:
    latitude, longitude = map(float, row[2].split(','))  # 假設緯經度在第三個欄位並以","分隔
    cursor.execute('''
        INSERT INTO my_table (shelter_ID, address, latitude, longitude, u_floor, p_available) 
        VALUES (%s, %s, %s, %s, %s, %s)
    ''', (row[0], row[1], latitude, longitude, int(row[3]), int(row[4])))

# 提交變更並關閉資料庫
conn.commit()
conn.close()

StopIteration: 

In [9]:
import psycopg2
import requests
import csv
import io

# 下載資料
url = "https://data.taipei/api/dataset/70a6216e-3730-4d1d-b334-62fca2dd71cd/resource/3bd658e7-8e8a-446b-8df5-89b2b896ff97/download"
response = requests.get(url)

# 確認回應狀態是否為 200（成功）
if response.status_code != 200:
    print(f"Failed to retrieve data, status code: {response.status_code}")
else:
    # 解析 CSV 資料
    taipei_csv_data = io.StringIO(response.text)
    reader = csv.reader(taipei_csv_data)

    # 檢查是否有資料
    try:
        header = next(reader)  # 跳過標題行
    except StopIteration:
        print("No data available in the CSV.")
    else:
        # 連接 PostgreSQL 資料庫
        conn = psycopg2.connect(
            dbname="postgres", 
            user="postgres", 
            password="mysecretpassword", 
            host="localhost", 
            port="5432"
        )
        cursor = conn.cursor()

        # 建立表格（如果尚未存在）
        cursor.execute('''
            CREATE TABLE IF NOT EXISTS my_table (
                shelter_ID TEXT,
                address TEXT,
                latitude FLOAT,
                longitude FLOAT,
                u_floor INTEGER,
                p_available INTEGER
            )
        ''')

        # 讀取並處理資料
        for row in reader:
            try:
                # 檢查緯經度欄位是否有效（假設緯經度在第 6 欄）
                lat_lon = row[5]
                if lat_lon:
                    latitude, longitude = map(float, lat_lon.split(','))  # 假設緯經度在第 6 欄並以","分隔
                    cursor.execute('''
                        INSERT INTO my_table (shelter_ID, address, latitude, longitude, u_floor, p_available) 
                        VALUES (%s, %s, %s, %s, %s, %s)
                    ''', (row[2], row[4], latitude, longitude, int(row[6]), int(row[7])))
                else:
                    print(f"Invalid latitude/longitude data in row {row}, skipping.")
            except ValueError as e:
                print(f"Error processing row {row}: {e}")
                continue

        # 提交變更並關閉資料庫
        conn.commit()
        conn.close()

Error processing row ['一般住宅', '公寓', 'WYA01050', '大有里', '臺北市大同區涼州街116號', '25.060459,121.509074', 'B01', '73', '大同分局', '']: invalid literal for int() with base 10: 'B01'
Error processing row ['一般住宅', '公寓', 'WYA01051', '大有里', '臺北市大同區環河北路一段313號', '25.059635,121.508738', 'B01', '80', '大同分局', '']: invalid literal for int() with base 10: 'B01'
Error processing row ['一般住宅', '私人住宅大樓', 'WYA01052', '大有里', '臺北市大同區環河北路一段343號', '25.060258,121.508605', 'B01', '400', '大同分局', '']: invalid literal for int() with base 10: 'B01'
Error processing row ['一般住宅', '私人住宅大樓', 'WYA01053', '大有里', '臺北市大同區迪化街一段238號', '25.059928,121.509314', 'B01', '320', '大同分局', '']: invalid literal for int() with base 10: 'B01'
Error processing row ['一般住宅', '私人住宅大樓', 'WYA01054', '大有里', '臺北市大同區安西街54號', '25.059633,121.509969', 'B01', '170', '大同分局', '']: invalid literal for int() with base 10: 'B01'
Error processing row ['一般住宅', '公寓', 'WYA01055', '大有里', '臺北市大同區安西街9巷11號', '25.059596,121.510396', 'B01', '34', '大同分局', '']: invalid literal